#     Text classification with Naive Bayes : feature selection with mutual information

## Notebook made by  

|** Name** | **Student id** | **email**|
|:- |:-|:-|
|. | | |
|  | |. |

### Pledge (taken from [Coursera's Honor Code](https://www.coursera.org/about/terms/honorcode) )



Put here a selfie with your photo where you hold a signed paper with the following text: (if this is team work, put two selfies here). The link must be to some place on the web, not to a local file. 

> My answers to homework, quizzes and exams will be my own work (except for assignments that explicitly permit collaboration).

>I will not make solutions to homework, quizzes or exams available to anyone else. This includes both solutions written by me, as well as any official solutions provided by the course staff.

>I will not engage in any other activities that will dishonestly improve my results or dishonestly improve/hurt the results of others.

<img src='link to your selfie'/>

### Note
* **Assignments without the selfies or completely filled in information will not be graded and receive 0 points.**


#  Text classification with Naive Bayes  
        
        
        
<h3>Abstract</h3>
<p>We will do **text classification** on a collection of Dutch parliamentary questions.
       </p>
<p>In dit notebook beperken we ons tot het bepalen van de **mutual information** scores, zoals beschereven in <http://nlp.stanford.edu/IR-book/html/htmledition/mutual-information-1.html> </p>
       
       
#### Data
* 40K kamervragen: <http://maartenmarx.nl/teaching/zoekmachines/LectureNotes/MySQL/KVR.csv.gz>
* 1K kamervragen <http://maartenmarx.nl/teaching/zoekmachines/LectureNotes/MySQL/KVR1000.csv.gz>

 

In [1]:
import nltk 
from pattern.nl import lemma  # works very bad for Dutch
import re
from collections import  Counter
import itertools
import sklearn
import pandas as pd
import numpy as np
from numpy import log2
from nltk.corpus import stopwords
dutchstop = set(stopwords.words('dutch'))

In [17]:

kvrdf= pd.read_csv('http://maartenmarx.nl/teaching/zoekmachines/LectureNotes/MySQL/KVR.csv.gz', 
                         compression='gzip', 
                         sep='\t', 
                         index_col=0, 
                       #  encoding='utf-8',
                         names=['jaar', 'partij','titel','vraag','antwoord','ministerie'])
print kvrdf.shape
kvrdf.head()

(40516, 6)


jaar partij  \
KVR1000.xml     1994   PvdA   
 KVR10000.xml   1999   PvdA   
 KVR10001.xml   1999     SP   
 KVR10002.xml   1999   PvdA   
 KVR10003.xml   1999   PvdA   

                                                           titel  \
KVR1000.xml     De vragen betreffen de betrouwbaarheid van de...   
 KVR10000.xml   Vragen naar aanleiding van berichten (uitzend...   
 KVR10001.xml   Vragen naar aanleiding van de berichten "Nede...   
 KVR10002.xml   Vragen over de gebrekkige opvang van verpleeg...   
 KVR10003.xml   Vragen over onbetrouwbaarheid van filemeldingen.   

                                                           vraag  \
KVR1000.xml     Hebt u kennisgenomen van het televisieprogram...   
 KVR10000.xml   Kent u de berichten over de situatie in de Me...   
 KVR10001.xml   Kent u de berichten «Nederland steunt de Soeh...   
 KVR10002.xml   Kent u het bericht over onderzoek van Nu91 me...   
 KVR10003.xml   Hebt u kennisgenomen van de berichten over de...   

                                                        antwoord  \
KVR1000.xml     Ja. Het bedoelde geluidmeetpunt is eigendom v...   
 KVR10000.xml                                                      
 KVR10001.xml                                                      
 KVR10002.xml   Ja. Het onderzoek van NU’91 wijst uit dat het...   
 KVR10003.xml   Ja. Nee. Door de waarnemers van het Algemeen ...   

                                       ministerie  
KVR1000.xml                 Verkeer en Waterstaat  
 KVR10000.xml                            Justitie  
 KVR10001.xml                           Financien  
 KVR10002.xml   Volksgezondheid, Welzijn en Sport  
 KVR10003.xml               Verkeer en Waterstaat

<h2>Exercise</h2>

<p>We will use the fields in the _ministerie_ column as our classes. 
    These are the ministeries to whom the question is addressed.
<br/>     
    Note that these labels are <strong>not normalized</strong>, see e.g. these counts   below

In [3]:
kvrdf.ministerie.value_counts().head(30)

 Justitie (JUS)                                                    3219
 Volksgezondheid, Welzijn en Sport (VWS)                           2630
 Buitenlandse Zaken (BUZA)                                         1796
 Verkeer en Waterstaat (VW)                                        1441
 Justitie                                                          1333
 Sociale Zaken en Werkgelegenheid (SZW)                            1231
 Onderwijs, Cultuur en Wetenschappen (OCW)                         1187
 Volkshuisvesting, Ruimtelijke Ordening en Milieubeheer (VROM)      984
 Financiën (FIN)                                                    960
 Volksgezondheid, Welzijn en Sport                                  951
 Economische Zaken (EZ)                                             946
 Buitenlandse Zaken                                                 753
 Binnenlandse Zaken en Koninkrijksrelaties (BZK)                    725
 Verkeer en Waterstaat                                          

# Exercises
 
* Normalize the values for "ministerie" and choose 10 ministeries to work with. Put these in a new column called `NormalizedMinisterie`.
* Let ook goed op spaties aan het begin en eind.
      
      

In [25]:
# Ik heb er 13 gekozen want die laatste drie leken me juist zo leuk.

topNChosenMinisteries=13

kvrdf['NormalizedMinisterie']= kvrdf.ministerie.str.replace(r' *\(.*','')
kvrdf['NormalizedMinisterie']=kvrdf.NormalizedMinisterie.str.strip() # remove leading and ending spaces
print kvrdf['NormalizedMinisterie'].value_counts().head(topNChosenMinisteries).sum()
kvrdf['NormalizedMinisterie'].value_counts().head(topNChosenMinisteries)

24824


Justitie                                                  4640
Volksgezondheid, Welzijn en Sport                         3597
Buitenlandse Zaken                                        2697
Verkeer en Waterstaat                                     2178
Sociale Zaken en Werkgelegenheid                          1861
Onderwijs, Cultuur en Wetenschappen                       1730
Volkshuisvesting, Ruimtelijke Ordening en Milieubeheer    1560
Financiën                                                 1403
Economische Zaken                                         1309
Binnenlandse Zaken en Koninkrijksrelaties                 1241
Landbouw, Natuurbeheer en Visserij                        1031
Defensie                                                   963
Vreemdelingenzaken en Integratie                           614
Name: NormalizedMinisterie, dtype: int64

In [26]:
# restrict to the top 13

print len(kvrdf)
kvrdf= kvrdf[kvrdf.NormalizedMinisterie.isin(kvrdf['NormalizedMinisterie'].value_counts().head(topNChosenMinisteries).index)]
kvrdf.shape

40516


(24824, 9)

# Tokenize

1. Voeg een kolom `vocabulair` toe met een lijst met alle unieke woorden die voorkomen in de tekst kolommen van een kamervraag.
    * lowercase de woorden
    * gooi getallen en punctuatie-tokens weg
    * neem geen woorden die in de NL stopwoorden lijst `dutchstop` zitten op
    * je kunt ook nog lemmatiseren
2. **Hint** 
    * Plak eerst alle tekst aan elkaar vast (let op!)
    * maak een functie die tokenize doet en al die dingen hierboven beschreven
    * pas die functie met `.apply` toe op de kolom met alle tekst
3. Dit kan wel even duren. Test dus op kleine aantallen, of op de kleine file.

In [7]:
lemma('basisschool')

'basisscholen'

In [ ]:
kvrdf['fulltext']= kvrdf.titel.astype(str)+' '+kvrdf.vraag.astype(str)+' '+kvrdf.antwoord.astype(str)


 
    

def tokenize(text, lemmatize=False):
    tokens=  [s.lower()  for s in set(nltk.word_tokenize(str(text).decode('utf-8')))
     if   re.match(r'^\w+$',s)  and 
            len(s) > 2
            and not re.match(r'^\d+$',s ) and 
         not s.lower() in dutchstop
            ]
    if not lemmatize:
        return list(set(tokens))
    if lemmatize:
         return list(lemma(w) for w in set(tokens))
        
# test

print kvrdf.fulltext.head(5).apply(tokenize)

kvrdf.fulltext.head(5).apply(lambda w:tokenize(w,lemmatize=True))

In [ ]:
%time kvrdf['vocabulair']= kvrdf.fulltext.apply(tokenize)

In [22]:
%time kvrdf['lemmatized_vocabulair']= kvrdf.fulltext.apply(lambda w:tokenize(w,lemmatize=True))

CPU times: user 4min 40s, sys: 3.42 s, total: 4min 43s
Wall time: 4min 44s


In [20]:
# Fast alternative 
def filter_voc(L):
    tokens=[s for s in L if len(s) > 2
            and not re.match(r'^\d+$',s ) and 
         not s in dutchstop
           ]
    return list(set(tokens))
%time tokens= (kvrdf.fulltext.str.lower().str.findall(r'\b\w+\b')).apply(filter_voc)

CPU times: user 44.2 s, sys: 433 ms, total: 44.6 s
Wall time: 44.9 s


In [27]:
# Even faster 
# lower case, length restrictie, remove pure digits, remove doubles,  remove dutchstop 

%time tokens= (kvrdf.fulltext.str.lower().str.replace(r'\b\d+\b','').str.replace(r'\b\w\w\b','').str.findall(r'\b\w+\b')).apply(lambda l:([w for w in  set(l) if not w in dutchstop]))

kvrdf['vocabulair']=tokens
tokens.head()



CPU times: user 12.9 s, sys: 208 ms, total: 13.1 s
Wall time: 13.5 s


/Users/admin/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


KVR1000.xml      [betrouwbaarheid, inderdaad, meter, bereiken, ...
 KVR10000.xml    [twijfels, bent, kennis, situatie, moeten, wel...
 KVR10002.xml    [gestaan, erom, volkskrant, wijze, protocollen...
 KVR10003.xml    [gezet, betrouwbaarheid, desbetreffende, waarn...
 KVR10004.xml    [rol, volkskrant, termijn, gepresenteerd, spoo...
Name: fulltext, dtype: object

# Pattern lemmatize is very dodgy for NL

In [ ]:
#kvrdf.lemmatized_vocabulair.head()

# Tel woorden voor elk Minsterie

* Gebruik `Counter` om voor elk Ministerie, **voor elk woord te tellen in hoeveel documenten dat woord voorkomt.**
* **Hints**
    * Loop over alle ministeries
    * voor elk ministerie pak de kolom vocabulair op, en concateneer alle lijsten tot 1 lijst
    * tel dan met `Counter`
    * Neem alleen woorden die in minimaal 10 documenten voorkomen
    * Lever uiteindelijk een dict op met Ministeries als sleutels en hun counters als waarden
    * Maak hier een dataframe van met `pd.DataFrame.from_dict`
        * de woorden zijn de rijen, en de Ministeries de kolommen


In [28]:
def makeCounters(Vocabulair,drempelwaarde=10):
    II= {}
    for mi in  set(kvrdf.NormalizedMinisterie.values):
        A= kvrdf[kvrdf.NormalizedMinisterie==mi][Vocabulair].values
        M= Counter([w  for l in A for w in l])
        Minimaal10={v:M[v] for v in M if M[v]>=drempelwaarde}
        II[mi]= Minimaal10
    return II

%time II= makeCounters('vocabulair')

for mi in II:
    print mi, len(II[mi])

CPU times: user 4.2 s, sys: 99.5 ms, total: 4.3 s
Wall time: 4.3 s
Volksgezondheid, Welzijn en Sport 7671
Defensie 2903
Sociale Zaken en Werkgelegenheid 4978
Justitie 8126
Binnenlandse Zaken en Koninkrijksrelaties 3677
Landbouw, Natuurbeheer en Visserij 3184
Financiën 4167
Volkshuisvesting, Ruimtelijke Ordening en Milieubeheer 4802
Buitenlandse Zaken 6030
Onderwijs, Cultuur en Wetenschappen 4581
Vreemdelingenzaken en Integratie 2101
Verkeer en Waterstaat 5634
Economische Zaken 4225


In [29]:
# Turn it into a dataframe 
%time IIdf=pd.DataFrame.from_dict(II)#.fillna(0)
IIdf.describe()

CPU times: user 109 ms, sys: 3.05 ms, total: 113 ms
Wall time: 113 ms


/Users/admin/anaconda/lib/python2.7/site-packages/numpy/lib/function_base.py:3834: RuntimeWarning: Invalid value encountered in percentile
  RuntimeWarning)


Binnenlandse Zaken en Koninkrijksrelaties  Buitenlandse Zaken  \
count                                3677.000000         6030.000000   
mean                                   50.447919           70.073632   
std                                    74.609997          132.822490   
min                                    10.000000           10.000000   
25%                                          NaN                 NaN   
50%                                          NaN                 NaN   
75%                                          NaN                 NaN   
max                                  1106.000000         2184.000000   

          Defensie  Economische Zaken    Financiën     Justitie  \
count  2903.000000        4225.000000  4167.000000  8126.000000   
mean     42.026180          53.996923    54.662827    90.829190   
std      57.124467          81.939572    82.836844   197.824251   
min      10.000000          10.000000    10.000000    10.000000   
25%            NaN                NaN          NaN          NaN   
50%            NaN                NaN          NaN          NaN   
75%            NaN                NaN          NaN          NaN   
max     766.000000        1057.000000  1089.000000  3808.000000   

       Landbouw, Natuurbeheer en Visserij  \
count                         3184.000000   
mean                            47.155779   
std                             63.995373   
min                             10.000000   
25%                                   NaN   
50%                                   NaN   
75%                                   NaN   
max                            762.000000   

       Onderwijs, Cultuur en Wetenschappen  Sociale Zaken en Werkgelegenheid  \
count                          4581.000000                       4978.000000   
mean                             59.431347                         65.586983   
std                              98.232193                        109.091074   
min                              10.000000                         10.000000   
25%                                    NaN                               NaN   
50%                                    NaN                               NaN   
75%                                    NaN                               NaN   
max                            1357.000000                       1501.000000   

       Verkeer en Waterstaat  Volksgezondheid, Welzijn en Sport  \
count            5634.000000                        7671.000000   
mean               66.653355                          87.797810   
std               118.804579                         181.457338   
min                10.000000                          10.000000   
25%                      NaN                                NaN   
50%                      NaN                                NaN   
75%                      NaN                                NaN   
max              1703.000000                        2965.000000   

       Volkshuisvesting, Ruimtelijke Ordening en Milieubeheer  \
count                                        4802.000000        
mean                                           59.704082        
std                                            95.210070        
min                                            10.000000        
25%                                                  NaN        
50%                                                  NaN        
75%                                                  NaN        
max                                          1236.000000        

       Vreemdelingenzaken en Integratie  
count                       2101.000000  
mean                          38.621133  
std                           45.112760  
min                           10.000000  
25%                                 NaN  
50%                                 NaN  
75%                                 NaN  
max                          518.000000

In [30]:
IIdf.tail()

Binnenlandse Zaken en Koninkrijksrelaties  Buitenlandse Zaken  \
zwitserland                                        NaN                22.0   
zwitserse                                          NaN                 NaN   
zwolle                                             NaN                 NaN   
zwolse                                             NaN                 NaN   
zzp                                                NaN                 NaN   

             Defensie  Economische Zaken  Financiën  Justitie  \
zwitserland       NaN               11.0        NaN      20.0   
zwitserse         NaN                NaN        NaN      11.0   
zwolle            NaN                NaN        NaN      60.0   
zwolse            NaN                NaN        NaN      11.0   
zzp               NaN                NaN        NaN       NaN   

             Landbouw, Natuurbeheer en Visserij  \
zwitserland                                 NaN   
zwitserse                                   NaN   
zwolle                                      NaN   
zwolse                                      NaN   
zzp                                         NaN   

             Onderwijs, Cultuur en Wetenschappen  \
zwitserland                                  NaN   
zwitserse                                    NaN   
zwolle                                      14.0   
zwolse                                       NaN   
zzp                                          NaN   

             Sociale Zaken en Werkgelegenheid  Verkeer en Waterstaat  \
zwitserland                               NaN                   14.0   
zwitserse                                 NaN                    NaN   
zwolle                                    NaN                   32.0   
zwolse                                    NaN                   12.0   
zzp                                      20.0                    NaN   

             Volksgezondheid, Welzijn en Sport  \
zwitserland                               18.0   
zwitserse                                  NaN   
zwolle                                    33.0   
zwolse                                    10.0   
zzp                                        NaN   

             Volkshuisvesting, Ruimtelijke Ordening en Milieubeheer  \
zwitserland                                                NaN        
zwitserse                                                  NaN        
zwolle                                                     NaN        
zwolse                                                     NaN        
zzp                                                        NaN        

             Vreemdelingenzaken en Integratie  
zwitserland                               NaN  
zwitserse                                 NaN  
zwolle                                    NaN  
zwolse                                    NaN  
zzp                                       NaN

# Hoeveel woorden hebben we eigenlijk? 

Bijna 4 miljoen tokens, en 15K unieke woorden verdeeld  over bijna 25.000 documenten, verdeeld over 13 ministeries

In [15]:


print IIdf.sum().sum()
print IIdf.shape
IIdf.sum()

4089793.0
(14873, 13)


Binnenlandse Zaken en Koninkrijksrelaties                 185497.0
Buitenlandse Zaken                                        422544.0
Defensie                                                  122002.0
Economische Zaken                                         228137.0
Financiën                                                 227780.0
Justitie                                                  738078.0
Landbouw, Natuurbeheer en Visserij                        150144.0
Onderwijs, Cultuur en Wetenschappen                       272255.0
Sociale Zaken en Werkgelegenheid                          326492.0
Verkeer en Waterstaat                                     375525.0
Volksgezondheid, Welzijn en Sport                         673497.0
Volkshuisvesting, Ruimtelijke Ordening en Milieubeheer    286699.0
Vreemdelingenzaken en Integratie                           81143.0
dtype: float64

# Welke woorden komen het meest voor?

In [31]:
IIdf.sum(axis=1).sort_values(ascending=False).head(10)

vragen        20052.0
bent          15988.0
welke         15361.0
aanleiding    13285.0
zoals         12865.0
bereid        11655.0
mening        11650.0
ten           11298.0
wel           10897.0
mogelijk      10559.0
dtype: float64

# Mutual information

Definieer de functie $I(U,C)$ zoals in vergelijking 13.16 in het IR book. Je kunt natuurlijk veel makkelijker 13.17 implementeren. 
* Definieer in de functie alle onderdelen $N, N_{11}, N_{1.}$, etc


In [32]:
# Dit kan veel mooier met lineaire algebra vanuit een klein dataframepje

def h(cel,sumV,sumH,N):
     return (cel/N)*log2((N*cel)/(sumV*sumH))
    


def I(U,C,df):
    try:
        N= IIdf.sum().sum()
        N11= df.loc[U][C]
        N1p= df.loc[U].sum()
        Np1= df[C].sum()
        N10= N1p-N11
        N01= Np1-N11
        N0p= N-N1p
        Np0= N-Np1
        N00= N0p-N01
        return    sum([ h(N11,N1p,Np1,N),
                      h(N10,N1p,Np0,N),
                      h(N01,N0p,Np1,N),
                      h(N00,N0p,Np0,N)
                       ]
                     )
    except:
        return 0

#test     
I('misdrijf','Justitie',IIdf), I('misdrij','Justitie',IIdf)

(7.5381481637955215e-05, 0)

In [33]:
def TopNMutualInformationWords(C,n):
    '''Give the top N words with the highest mutual information score for class C'''
    df= pd.DataFrame.from_dict({w:I(w,C,IIdf) for w in IIdf[C].dropna().index}, orient='index')
    df.sort_values(0,ascending=False, inplace=True)
    df.columns= ['Mutual Information']
    return df.head(n)
 
%time TopNMutualInformationWords('Justitie',20)
 

CPU times: user 12.1 s, sys: 191 ms, total: 12.3 s
Wall time: 12.5 s


Mutual Information
justitie                    0.000401
politie                     0.000245
openbaar                    0.000213
verdachte                   0.000201
procureurs                  0.000183
strafbare                   0.000182
vervolging                  0.000179
wetboek                     0.000163
strafrechtelijk             0.000160
strafvordering              0.000154
officier                    0.000144
verdachten                  0.000139
strafrecht                  0.000134
feiten                      0.000131
opsporing                   0.000128
rechter                     0.000128
justiti                     0.000125
strafzaak                   0.000120
strafrechtelijke            0.000119
strafbaar                   0.000118

In [34]:
for mi in list(set(kvrdf.NormalizedMinisterie.values)):
    print mi,'\n', TopNMutualInformationWords(mi,10),'\n'

Defensie 
             Mutual Information
defensie               0.000516
militairen             0.000293
militaire              0.000220
koninklijke            0.000212
krijgsmacht            0.000211
militair               0.000203
commandant             0.000145
luchtmacht             0.000117
eenheden               0.000102
marine                 0.000096 

Sociale Zaken en Werkgelegenheid 
            Mutual Information
sociale               0.000314
werknemers            0.000304
arbeid                0.000258
werkgevers            0.000256
szw                   0.000245
wao                   0.000227
uitkering             0.000216
werkgever             0.000191
werknemer             0.000156
uwv                   0.000150 

Justitie 
                 Mutual Information
justitie                   0.000401
politie                    0.000245
openbaar                   0.000213
verdachte                  0.000201
procureurs                 0.000183
strafbare                  0.0001

# Try out:  Colocations of bigrammen

Zie <http://www.nltk.org/howto/collocations.html>

 

In [35]:
mi='Justitie'
A= kvrdf[kvrdf.NormalizedMinisterie==mi].fulltext 
A_all= ' '.join(A.values).decode('utf-8')
tokens= nltk.tokenize.wordpunct_tokenize(A_all)
B = nltk.Text(tokens)





In [36]:
# werkt niet echt goed, want filtert er geen NL stopwoorden uit
B.collocations()

van het; Openbaar Ministerie; naar aanleiding; waarom niet; openbaar
ministerie; ten aanzien; Aanhangsel Handelingen; mening dat;
betrekking tot; van een; Tweede Kamer; van van; Vragen naar; kan
worden; aanleiding van; met betrekking; strafbare feiten; het
Openbaar; feit dat; dan wel


In [37]:
from nltk.collocations import * 
bigram_measures = nltk.collocations.BigramAssocMeasures()

In [38]:
>>> word_fd = nltk.FreqDist(tokens)
>>> bigram_fd = nltk.FreqDist(nltk.bigrams(tokens))
>>> finder = BigramCollocationFinder(word_fd, bigram_fd)

In [39]:
finder.apply_freq_filter(100)
finder.apply_word_filter(lambda w: w in dutchstop or len(w)<3 or re.search(r'^\W+$',w))
scored = finder.score_ngrams(bigram_measures.pmi)

In [40]:

scored[:30]
#sorted(bigram for bigram, score in scored )

[((u'Sri', u'Lanka'), 14.334247343063975),
 ((u'Verenigd', u'Koninkrijk'), 13.770043402509613),
 ((u'Ter', u'Apel'), 13.120122537711127),
 ((u'persoonlijke', u'levenssfeer'), 13.014957486638092),
 ((u'Koninklijke', u'Marechaussee'), 12.6041932359635),
 ((u'Dienst', u'Justiti'), 12.55619998538745),
 ((u'Holland', u'Casino'), 12.27312889617636),
 ((u'centrale', u'autoriteit'), 12.21993631683266),
 ((u'NRC', u'Handelsblad'), 12.20586418610441),
 ((u'Verenigde', u'Staten'), 12.171037334864451),
 ((u'Nationale', u'Recherche'), 12.13859977696005),
 ((u'alleenstaande', u'minderjarige'), 12.029608731798323),
 ((u'voorlopige', u'hechtenis'), 11.992737081233336),
 ((u'seksueel', u'misbruik'), 11.992411369522582),
 ((u'Den', u'Haag'), 11.8970289893151),
 ((u'Den', u'Bosch'), 11.887777649381626),
 ((u'kort', u'geding'), 11.755647446233333),
 ((u'rechterlijke', u'macht'), 11.752291188474594),
 ((u'Indiener', u'vraagt'), 11.635066411357236),
 ((u'Algemeen', u'Overleg'), 11.607257418406245),
 ((u'inz